# Impact analysis of neutering the `SELFDESTRUCT` opcode in Ethereum

## WORK IN PROGRESS

This report is a work in progress. I will eventually release code needed to reproduce the results.

# Introduction

`SELFDESTRUCT` is an opcode which causes a contract to delete itself, meaning both code and storage are deleted from the state tree, and all ETH in the contract are sent to a specified address. It turns out that `SELFDESTRUCT` [has several drawbacks](https://hackmd.io/@vbuterin/selfdestruct). Most urgently, allowing contracts to selfdestruct causes complexities when switching to Verkle trees. The [current proposal for Verkle tries](https://notes.ethereum.org/@vbuterin/verkle_tree_eip#Miscellaneous) requires neutering the opcode, meaning that the opcode is renamed to `SENDALL` and the only thing it does is to send the contract balance to the specified address. In this report we study the uses of `SELFDESTRUCT` in contracts deployed to mainnet, and analyze how such a neutering might affect existing use cases.

# Terminology

If a contract is selfdestructed, and later a new contract is initialized at the same address, we will count these as separate contracts having the same address. A contract is either **active** if it hasn't selfdestructed, or **selfdestructed**. The **bytecode** of a contract will always mean the deployed bytecode it had when it was first initialized, even if it was later selfdestructed. An **ephemeral** contract is a contract that was initialized and selfdestructed in the same transaction.

In [1]:
from IPython.display import HTML
HTML('''<script>
code_show=true; 
function code_toggle() {
 if (code_show){
 $('div.input').hide();
 } else {
 $('div.input').show();
 }
 code_show = !code_show
} 
$( document ).ready(code_toggle);
</script>
<form action="javascript:code_toggle()"><input type="submit" value="Click here to toggle on/off the raw code."></form>''')

In [2]:
import psycopg2 as pg
import pandas as pd
from ipyaggrid import Grid
from matplotlib import pyplot as plt
from matplotlib.pyplot import figure
from IPython.display import display, Markdown, Code
from pygments.formatters import HtmlFormatter
from pygments import highlight
from pygments.lexers import SolidityLexer

In [3]:
conn = pg.connect(database='eth')

In [4]:
template = '''
<style>
{}
</style> {}
'''

def show_code(code, lineStart=1, lineEnd='end'):
    lines = code.split('\n')
    if lineEnd == 'end':
        lineEnd = len(lines)+1
    lines = lines[lineStart-1:lineEnd]
    codeSegment = '\n'.join(lines)
    formatter = HtmlFormatter(linenos='inline', linenostart=lineStart, cssclass='pygments')

    html_code = highlight(codeSegment, SolidityLexer(), formatter)
    css = formatter.get_style_defs('.pygments')

    html = template.format(css, html_code)

    display(HTML(html))

def show_contract_code(address, lineStart=1, lineEnd='end'):
    code = pd.read_sql('''select solidity_code from init left join code on (code_hash = code.hash) where address = '{}' and solidity_code is not null limit 1;'''.format(address), conn)
    show_code(code['solidity_code'][0], lineStart, lineEnd)

In [5]:
block_number = int(pd.read_sql('''select max(block_number) from init;''', conn)['max'])

In [6]:
display(Markdown('# Analysis \n(as of block number {})'.format(block_number)))

# Analysis 
(as of block number 12799316)

In [8]:
contract_count = int(pd.read_sql('''select sum(num_children) from creator;''', conn)['sum'])
selfdestructed_count = int(pd.read_sql('''select sum(num_selfdestructed_children) from creator;''', conn)['sum'])
active_count = contract_count - selfdestructed_count

display(Markdown('There have been a total of {} contract deployments on Ethereum Mainnet. Out of those, {} have selfdestructed, and {} are still active.'.format(f'{contract_count:,}', f'{selfdestructed_count:,}', f'{active_count:,}')))

There have been a total of 45,689,592 contract deployments on Ethereum Mainnet. Out of those, 25,146,002 have selfdestructed, and 20,543,590 are still active.

In the following table, we show all accounts who have deployed at least one contract that selfdestructed, along with some summaries about its child contracts.

In [9]:
df = pd.read_sql('''select is_contract, name, encode(address, 'hex') as address, num_children, num_distinct_children, num_selfdestructed_children, num_ephemeral_children, unique_children_addresses, unique_children_addresses_with_redeployments, num_children_at_address_with_redeployments from (select distinct on (address) * from creator left join init using (address) left join code on (code_hash = code.hash) order by address, instance_num desc) t where num_selfdestructed_children > 0 order by num_children desc;''', conn)

In [10]:
helpers_custom = '''
helpersCustom.urlRendering = function(params) {
      let accType;
      if (params.data.is_contract == true) {
          accType = "📄";
        } else {
          accType = "🙂";
      }
      const shortAddr = accType + params.value.substring(0,15)
      return `<a href="https://etherscan.io/address/0x${params.value}">${shortAddr}...</a>`;
    };
'''

In [11]:
column_defs = [
 {'field': 'is_contract', 'hide' : 'True'},
 {'field': 'name', 'headerName': 'Creator name', 'pinned': 'left'},
 {'field': 'address', 'headerName': 'Creator address', 'pinned': 'left', 'width': 100, 'cellRenderer': 'helpers.urlRendering'},
 {'field': 'num_children', 'headerName': 'Contracts'},
 {'field': 'num_distinct_children', 'headerName': 'Bytecodes'},
 {'field': 'num_selfdestructed_children', 'headerName': 'Selfdestructed contracts'},
 {'field': 'num_ephemeral_children', 'headerName': 'Ephemeral contracts'},
 {'field': 'unique_children_addresses', 'headerName': 'Addresses'},
 {'field': 'unique_children_addresses_with_redeployments', 'headerName': 'Addresses with reinits'},
 {'field': 'num_children_at_address_with_redeployments', 'headerName': 'Contracts at addresses with reinits'}]

grid_options = {
    'columnDefs' : column_defs,
    'enableSorting' : True,
    'onGridReady':'onGridReady'
}

Grid(grid_data=df, grid_options=grid_options, js_helpers_custom = helpers_custom, export_csv=True,quick_filter=True,columns_fit="auto")

Grid(columns_fit='auto', compress_data=True, export_mode='disabled', height='350px', js_helpers_custom='\nhelp…

Symbols: 📄 Contract 🙂 EOA

## Redeployed contracts

In [12]:
redeployed_contracts = pd.read_sql('''select is_contract, name, encode(address, 'hex') as address, num_children, num_distinct_children, num_selfdestructed_children, num_ephemeral_children, unique_children_addresses, unique_children_addresses_with_redeployments, num_children_at_address_with_redeployments from (select distinct on (address) * from creator left join init using (address) left join code on (code_hash = code.hash) order by address, instance_num desc) t where num_children_at_address_with_redeployments > 0 order by num_children_at_address_with_redeployments desc;''', conn)
display(Markdown('''
Redeployed contracts are contracts that have been deployed at the same address as a contract that has selfdestructed. There are {} contracts that have redeployed a child contract at least once. They are all listed in the following table.
'''.format(len(redeployed_contracts))
))
Grid(grid_data=redeployed_contracts, grid_options=grid_options, js_helpers_custom = helpers_custom, export_csv=True,quick_filter=True,columns_fit="auto")


Redeployed contracts are contracts that have been deployed at the same address as a contract that has selfdestructed. There are 123 contracts that have redeployed a child contract at least once. They are all listed in the following table.


Grid(columns_fit='auto', compress_data=True, export_mode='disabled', height='350px', js_helpers_custom='\nhelp…

In [13]:
#fig, ax = plt.subplots(figsize=(12,8), dpi= 100, facecolor='w', edgecolor='k')
#x = (df['num_children'] - df['num_children_at_address_with_redeployments'])[df['num_children_at_address_with_redeployments'] > 0] + 1
#y = df['num_children_at_address_with_redeployments'][df['num_children_at_address_with_redeployments'] > 0] + 1
#ax.scatter(x=x, y=y)

#for i, txt in df['name'][df['num_children_at_address_with_redeployments'] > 0].iteritems():
#    ax.annotate(txt, (x[i], y[i]))

#ax.set_yscale('log')
#ax.set_xscale('log')
#ax.set_xlabel('Number of child contracts deployed at addresses with reinits')
#ax.set_ylabel('Number of child contracts deployed at addresses without reinits')


#plt.show()

### PineCore

In [14]:
pinecore = pd.read_sql('''select * from creator where address = '\\xd412054cca18a61278ced6f674a526a6940ebd84';''', conn)

display(Markdown('''
As seen in the table above, [PineCore](https://etherscan.io/address/0xd412054cca18a61278ced6f674a526a6940ebd84) is the contract that has redeployed the largest number of contracts, and where the source code is available at etherscan. This contract has deployed {} contracts at {} distinct addresses. {} of the child contracts are deployed at addresses that have redeployments, and there are {} child addresses that have redeployed contracts. All of the child contracts are ephemeral, and all have the same bytecode.
'''.format(
    pinecore['num_children'][0]
    , pinecore['unique_children_addresses'][0]
    , pinecore['num_children_at_address_with_redeployments'][0]
    , pinecore['unique_children_addresses_with_redeployments'][0]
)))


As seen in the table above, [PineCore](https://etherscan.io/address/0xd412054cca18a61278ced6f674a526a6940ebd84) is the contract that has redeployed the largest number of contracts, and where the source code is available at etherscan. This contract has deployed 6959 contracts at 6596 distinct addresses. 622 of the child contracts are deployed at addresses that have redeployments, and there are 259 child addresses that have redeployed contracts. All of the child contracts are ephemeral, and all have the same bytecode.


#### How PineCore uses `SELFDESTRUCT`, and why neutering `SELFDESTRUCT` would create a security risk to its users
PineCore is part of [Pine.finance](https://medium.com/@pine_eth/pine-finance-an-amm-orders-engine-525fe1f1b1eb), which is an AMM orders engine. In short, the contract works as follows. Traders create orders by sending tokens to a account with a deterministic address, called a *vault*. Later, relayers may execute the order by calling the PineCore contract. If some conditions pre-specified by the trader are met, PineCore does the following in one transaction:

1. PineCore creates a contract at the deterministic address using `CREATE2` having the following call-forwarding code

In [15]:
show_code('''
def _fallback() payable:
    call cd[56] with:
        funct call.data[0 len 4]
        gas cd[56] wei
        args call.data[4 len 64]
    selfdestruct(tx.origin)
''')

2. This newly created contract is called with instructions on how to execute an order.
3. The contract executes the order, sending the new funds to the user who created the order, and selfdestructs.

Note that it is currently possible to create new orders by sending tokens to the same vault that has been used earlier. This would lead to a security risk if `SELFDESTRUCT` is neutered; sending tokens to a used vault would enable anyone to steal the users tokens, since the vault is still active with the call-forwarding code. Anyone could then call the vault and send the users token to themselves.

#### Possible solutions

1. Ask the creators of such contracts to deploy updated contracts that fixes this security risk.
2. Allow selfdestructing a contract if it was created in the same transaction, and neuter `SELFDESTRUCT` in all other cases.